In [1]:
import os, sys, json, datetime, re  # Provides OS-dependent functionality, system-specific parameters, JSON handling, and date/time manipulation
import pandas as pd             # Provides data structures and data analysis tools
import numpy as np              # Supports large, multi-dimensional arrays and matrices
import requests
import time
from tqdm import tqdm
import glob as glob

#thi data contants
from cprl_functions.defined_functions import *
from cprl_functions.state_capture import *
from cprl_functions.text_printing import bordered
# from cprl_functions.data_packet_defs import *


def pop_column(df, label):
    popped_col = df.pop(label)
    df.insert(0,label,popped_col)
    return df

In [7]:
disadvantaged_files = glob.glob(r"C:/Users/clutz/downloads/*disadvantaged.csv")
print(disadvantaged_files)
dis_ad_dfs = []
for file in disadvantaged_files:
    df = pd.read_csv(file)
    dis_ad_dfs.append(df)

dis_ad_df = pd.concat(dis_ad_dfs).reset_index()
dis_ad_df = dis_ad_df.sort_values(by = 'School Name')
dis_ad_df['full_code'] = dis_ad_df['Division Number'].astype(str)+ "-" + dis_ad_df['School Number'].astype(str)
pop_column(dis_ad_df,'full_code')
print(dis_ad_df.to_string())
dis_ad_df.to_csv("C:/Users/clutz/Downloads/dis_el_data.csv", index=False)


['C:/Users/clutz/downloads\\2324_el_disadvantaged.csv', 'C:/Users/clutz/downloads\\2324_el_not_disadvantaged.csv', 'C:/Users/clutz/downloads\\2425_el_disadvantaged.csv', 'C:/Users/clutz/downloads\\2425_el_not_disadvantaged.csv']
     full_code  index School Year  Division Number                    Division Name  School Number                                                    School Name          Subject Disadvantaged English Learners Test Source             Test  Pass Rate
2530    75-330   1004   2023-2024               75           Prince William County             330                                        A. Henderson Elementary  English:Reading             N                Y         SOL  English Reading        <50
4053    75-330   1061   2024-2025               75           Prince William County             330                                        A. Henderson Elementary  English:Reading             Y                Y         SOL  English Reading      62.22
5578    75-330   1053

In [148]:
enroll_files = [r'c:\Users\clutz\Downloads\non_el_fall_membership_statistics.csv', r'c:\Users\clutz\Downloads\fall_membership_statistics.csv', r'c:\Users\clutz\Downloads\non_el_23-24fall_membership_statistics.csv', r'c:\Users\clutz\Downloads\23-24_fall_membership_statistics.csv']
enroll_dfs = []
for file in enroll_files:
    df = pd.read_csv(file)
    enroll_dfs.append(df)

enrollment_df = pd.concat(enroll_dfs).reset_index()
enrollment_df = enrollment_df.sort_values(by = 'School Name')
enrollment_df['full_code'] = enrollment_df['Division Number'].astype(str)+ "-" + enrollment_df['School Number'].astype(str)
print(enrollment_df.to_string())


      index School Year  Division Number                   Division Name  School Number                                                    School Name English Learners          FT Count          PT Count       Total Count full_code
4885   1278   2023-2024               75           Prince William County            330                                        A. Henderson Elementary                N               664               NaN               664    75-330
3067   1204   2024-2025               75           Prince William County            330                                        A. Henderson Elementary                Y               125               NaN               125    75-330
6671   1195   2023-2024               75           Prince William County            330                                        A. Henderson Elementary                Y               130               NaN               130    75-330
1275   1275   2024-2025               75           Prince William County

In [150]:
def get_full_code(string):
    results = enrollment_df[enrollment_df['School Name']==string]
    full_code_fetch = get_col_uniq_vals(results['full_code'])
    if full_code_fetch is None:
        print(full_code_fetch)
    try:
        full_code = full_code_fetch[0]
        return full_code
    except:
        return None
        print(string)
        print(full_code_fetch)

In [151]:
qual_prof_file = r'c:\Users\clutz\Downloads\Enrollment.csv'
qual_prf_df = pd.read_csv(qual_prof_file)
qual_prf_df = qual_prf_df.dropna(subset='Grade')
qual_prf_df['full_code'] = qual_prf_df['School'].apply(get_full_code)

# for i,e in enumerate(qual_prf_df['School']):
    

In [152]:

grouped = qual_prf_df.groupby(['Division', 'School', 'full_code']).agg({
    'Grade': lambda x: "|".join(x)
}).reset_index()

grouped


Division                   School full_code  \
0     Accomack County Public Schools    Accawmacke Elementary     1-701   
1     Accomack County Public Schools             Arcadia High     1-540   
2     Accomack County Public Schools          Arcadia Middle      1-704   
3     Accomack County Public Schools  Chincoteague Elementary      1-80   
4     Accomack County Public Schools        Chincoteague High     1-580   
...                              ...                      ...       ...   
1789      York County Public Schools   Waller Mill Elementary    98-220   
1790      York County Public Schools                York High     98-30   
1791      York County Public Schools       York River Academy    98-335   
1792      York County Public Schools      Yorktown Elementary    98-210   
1793      York County Public Schools          Yorktown Middle     98-60   

                     Grade  
0     PK|KG|01|02|03|04|05  
1           PG|09|10|11|12  
2                 06|07|08  
3     PK|KG|01|02|03|04|05  
4     06|07|08|09|10|11|12  
...                    ...  
1789  PK|KG|01|02|03|04|05  
1790        PG|09|10|11|12  
1791           09|10|11|12  
1792  PK|KG|01|02|03|04|05  
1793              06|07|08  

[1794 rows x 4 columns]

In [153]:
# level_dict = {}
# for row in grouped.itertuples():
#     grades = row.Grade.split('|')
#     grades = [int(x) for x in grades if x.isnumeric()]
#     levels = []
#     if any(x for x in grades if x <6):
#         levels.append('elementary')
#     elif any(x for x in grades if x <9 and x>5):
#         levels.append('middle')
#     elif all(x for x in grades if x >8):
#         levels.append('high')
#     else:
#         continue

#     if 'Cora' in row.School:
#         print('__________________')
#         print(row.School)
#         print(levels)
#         print(grades)
#     elif len(levels)==1:
#         level = levels[0]
#         if row.full_code not in level_dict.keys():
#             level_dict[row.full_code]=level

# # qual_prf_df['level']

In [154]:
for l,v in level_dict.items():
    print(repr(l))
    print(type(l))
    print(v)
    # if str(v) == 'nan':
    #     print(l)
    #     print(v)

'1-1'
<class 'str'>
elementary
'2-2'
<class 'str'>
elementary
'75-75'
<class 'str'>
elementary
'101-101'
<class 'str'>
elementary
'3-3'
<class 'str'>
high
'4-4'
<class 'str'>
elementary
'5-5'
<class 'str'>
elementary
'6-6'
<class 'str'>
high
'36-36'
<class 'str'>
elementary
'7-7'
<class 'str'>
elementary
'123-123'
<class 'str'>
elementary
'53-53'
<class 'str'>
elementary
'37-37'
<class 'str'>
elementary
'43-43'
<class 'str'>
elementary
'8-8'
<class 'str'>
high
'9-9'
<class 'str'>
middle
'10-10'
<class 'str'>
elementary
'30-30'
<class 'str'>
high
'29-29'
<class 'str'>
middle
'54-54'
<class 'str'>
elementary
'11-11'
<class 'str'>
elementary
'12-12'
<class 'str'>
elementary
'21-21'
<class 'str'>
elementary
'102-102'
<class 'str'>
high
'13-13'
<class 'str'>
high
'14-14'
<class 'str'>
elementary
'15-15'
<class 'str'>
elementary
'103-103'
<class 'str'>
elementary
'16-16'
<class 'str'>
elementary
'17-17'
<class 'str'>
elementary
'18-18'
<class 'str'>
high
'127-127'
<class 'str'>
elementary
'1

In [10]:
#apply level
# df_all = pd.read_csv('df_all.csv')
files = [r'c:\Users\clutz\Downloads\assessment_statistics_eln_soltests_reading.csv ',r'c:\Users\clutz\Downloads\2324assessment_statistics_not_eln_soltests_reading.csv ',r'c:\Users\clutz\Downloads\2324assessment_statistics_eln_soltests_reading.csv ',r'c:\Users\clutz\Downloads\assessment_statistics_not_eln_soltests_reading.csv']
all_data_df = pd.concat(
    map(pd.read_csv, files), ignore_index=True)
print(all_data_df.to_string(max_colwidth=30))


     School Year  Division Number                  Division Name  School Number                    School Name          Subject English Learners Test Source  Pass Rate
0      2024-2025                1               Accomack County             701          Accawmacke Elementary  English:Reading                Y         SOL      59.42
1      2024-2025                1               Accomack County             540                   Arcadia High  English:Reading                Y         SOL      54.55
2      2024-2025                1               Accomack County             704                Arcadia Middle   English:Reading                Y         SOL      34.00
3      2024-2025                1               Accomack County              80        Chincoteague Elementary  English:Reading                Y         SOL        <50
4      2024-2025                1               Accomack County             600            Kegotank Elementary  English:Reading                Y         SOL    

In [ ]:

all_data_df.columns = [x.lower().replace(' ', "_").strip() for x in all_data_df.columns]
all_data_df['full_code'] = all_data_df['division_number'].astype(str)+"-"+all_data_df['school_number'].astype(str)
print(all_data_df.columns)
# all_data_df = all_data_df.iloc[:,1:]
all_data_df['level'] = np.nan
idk = []
for row in all_data_df.itertuples(index= True):
    school = row.school_name
    if school in idk:
        continue
    hs_match = re.search(r'[Hh]igh', str(school))
    ms_match = re.search(r'[Mm]iddle|[Ii]ntermed', str(school))
    es_match = re.search(r'[Ee]le(mentary)?', str(school))

    if hs_match:
        all_data_df.loc[row.Index, 'level'] = 'HS'
    elif ms_match:
        all_data_df.loc[row.Index, 'level'] = 'MS'
    elif es_match:
        all_data_df.loc[row.Index, 'level'] = 'ES'
    else:
        idk.append(row.full_code)
        print(row)

In [156]:
print(all_data_df.columns)
enrollment_df.columns = [x.lower().strip().replace(' ','_') for x in enrollment_df.columns]
print(enrollment_df.columns)

Index(['school_year', 'division_number', 'division_name', 'school_number',
       'school_name', 'subject', 'english_learners', 'test_source',
       'pass_rate', 'full_code', 'level'],
      dtype='object')
Index(['index', 'school_year', 'division_number', 'division_name',
       'school_number', 'school_name', 'english_learners', 'ft_count',
       'pt_count', 'total_count', 'full_code'],
      dtype='object')


In [160]:
print(all_data_df.sort_values(by='school_name').head().to_string())
print(enrollment_df.sort_values(by='school_name').head().to_string())
# enrollment_df



     school_year  division_number           division_name  school_number                 school_name          subject english_learners test_source  pass_rate full_code level
6229   2024-2025               75  Prince William County             330     A. Henderson Elementary  English:Reading                N         SOL      85.22    75-330    ES
4518   2023-2024               75  Prince William County             330     A. Henderson Elementary  English:Reading                Y         SOL      36.96    75-330    ES
1121   2024-2025               75  Prince William County             330     A. Henderson Elementary  English:Reading                Y         SOL      61.76    75-330    ES
2844   2023-2024               75  Prince William County             330     A. Henderson Elementary  English:Reading                N         SOL      85.59    75-330    ES
3710   2023-2024               24        Culpeper County             240  A.G. Richardson Elementary  English:Reading             

In [158]:
def get_level(string):
    results = level_dict.get(string)
    print(repr(string))
    print(type(string))
    return results

In [163]:

merge_df = pd.merge(
    all_data_df,
    enrollment_df[['full_code', 'school_year','english_learners', 'total_count']],
    on=['full_code', 'english_learners', 'school_year'],
    how='left'
)
# # Get just the columns that are NOT in all_data_df
# columns_to_add = [col for col in enrollment_df.columns if col not in all_data_df.columns or col == 'full_code' or col == 'english_learners']

# # Merge using only the necessary columns
# merge_df = pd.merge(
#     all_data_df,
#     enrollment_df[columns_to_add],
#     on=['full_code', 'english_learners'],
#     how='left'
# )
# merge_df = pd.merge(all_data_df, enrollment_df, on=['full_code','english_learners'], how='left')
print(merge_df.sort_values(by='school_name').to_string())

     school_year  division_number                    division_name  school_number                                                    school_name          subject english_learners test_source  pass_rate full_code level       total_count
6229   2024-2025               75           Prince William County             330                                        A. Henderson Elementary  English:Reading                N         SOL      85.22    75-330    ES               667
4518   2023-2024               75           Prince William County             330                                        A. Henderson Elementary  English:Reading                Y         SOL      36.96    75-330    ES               130
1121   2024-2025               75           Prince William County             330                                        A. Henderson Elementary  English:Reading                Y         SOL      61.76    75-330    ES               125
2844   2023-2024               75           Prince Willi

In [166]:
import pandas as pd

# Assuming your dataframe is called 'df'

# Create a pivot table
df_wide = merge_df.pivot_table(
    index=[
        'division_number', 
        'division_name', 
        'school_number', 
        'school_name', 
        'subject', 
        'english_learners', 
        'test_source',
        'full_code',
        'level'
    ],
    columns='school_year',
    values=['pass_rate', 'total_count'],
    aggfunc='first'  # Use 'first' since there should be one value per group
).reset_index()

# Flatten the multi-level column names
df_wide.columns = ['_'.join(col).strip('_') if col[1] else col[0] 
                    for col in df_wide.columns.values]

# Rename columns to your preferred format
# This maps 'pass_rate_2024-2025' to 'pass_rate_25', etc.
df_wide = df_wide.rename(columns={
    'pass_rate_2024-2025': 'pass_rate_25',
    'pass_rate_2023-2024': 'pass_rate_24',
    'total_count_2024-2025': 'enrollment_25',
    'total_count_2023-2024': 'enrollment_24'
})
print(df_wide.sort_values(by='school_name').to_string())
# print(df_wide.head())
# print("\nColumn names:", df_wide.columns.tolist())

      division_number                    division_name  school_number                                                    school_name          subject english_learners test_source full_code level pass_rate_24 pass_rate_25     enrollment_24     enrollment_25
1843               75           Prince William County             330                                        A. Henderson Elementary  English:Reading                N         SOL    75-330    ES        85.59        85.22               664               667
1844               75           Prince William County             330                                        A. Henderson Elementary  English:Reading                Y         SOL    75-330    ES        36.96        61.76               130               125
490                24                 Culpeper County             240                                     A.G. Richardson Elementary  English:Reading                Y         SOL    24-240    ES          <50        29.63         

In [167]:
# cleaned_df = all_data_df[~all_data_df['level'].isnull()].reset_index(drop=True)
# reading_df = all_data_df[all_data_df['subject'].str.contains('English:Reading')].reset_index(drop=True)
reading_df = pop_column(df_wide, 'full_code').reset_index(drop=True)
reading_df

full_code  division_number     division_name  school_number  \
0         1-70                1  Accomack County              70   
1         1-70                1  Accomack County              70   
2         1-80                1  Accomack County              80   
3         1-80                1  Accomack County              80   
4        1-540                1  Accomack County             540   
...        ...              ...               ...            ...   
3385    202-22              202   Colonial Beach              22   
3386   207-280              207       West Point             280   
3387   207-280              207       West Point             280   
3388   207-290              207       West Point             290   
3389   207-290              207       West Point             290   

                    school_name          subject english_learners test_source  \
0                   Nandua High  English:Reading                N         SOL   
1                   Nandua High  English:Reading                Y         SOL   
2       Chincoteague Elementary  English:Reading                N         SOL   
3       Chincoteague Elementary  English:Reading                Y         SOL   
4                  Arcadia High  English:Reading                N         SOL   
...                         ...              ...              ...         ...   
3385  Colonial Beach Elementary  English:Reading                Y         SOL   
3386      West Point Elementary  English:Reading                N         SOL   
3387      West Point Elementary  English:Reading                Y         SOL   
3388     West Point Middle/High  English:Reading                N         SOL   
3389     West Point Middle/High  English:Reading                Y         SOL   

     level pass_rate_24 pass_rate_25     enrollment_24     enrollment_25  
0       HS        86.44        87.50               507               473  
1       HS          <50        70.00                47                61  
2       ES        75.49        64.86               223               239  
3       ES          <50          <50                 <                 <  
4       HS        82.20        86.29               573               561  
...    ...          ...          ...               ...               ...  
3385    ES          <50          NaN                 <               NaN  
3386    ES        84.71        88.00               380               397  
3387    ES          >50          >50                 <                11  
3388    HS        82.16        81.57               445               427  
3389    HS          <50          <50                 <                 <  

[3390 rows x 13 columns]

In [168]:
# all_codes = all_codes.sort()
# eln_df = pd.read_clipboard()
eln_df = pd.read_csv('eln_schools.csv')
eln_df.columns = [x.lower().replace(' ', "_").strip() for x in eln_df.columns]

eln = pop_column(eln_df, 'full_code')
all_codes = get_col_uniq_vals(eln_df['full_code'])
print(all_codes)
# print(type(all_codes))

['123-3105', '130-640', '17-450', '1-704', '7-350', '50-180', '33-1311', '124-210', '130-600', '77-560', '144-420', '112-450', '88-381', '88-506', '144-30', '88-370', '7-90', '115-130', '124-280', '17-630', '7-200', '144-31', '124-150', '2-40', '123-1510', '118-570', '115-170', '74-340', '108-40', '118-760']


In [169]:
reading_df['eln_school?'] = False
for row in reading_df.itertuples(index=True):
    # print(row.full_code)
    if any(x for x in all_codes if row.full_code in all_codes):
        reading_df.loc[row.Index, 'eln_school?'] = True
        print("got one")

got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one
got one


In [170]:
import pandas as pd

# Dictionary mapping Virginia independent cities to their surrounding/associated counties
# Note: Virginia independent cities are not part of any county legally,
# but this maps them to the county they're geographically associated with or surrounded by
city_to_county_map = {
    'Alexandria City': 'Arlington County',
    'Bristol City': 'Washington County',
    'Buena Vista City': 'Rockbridge County',
    'Charlottesville City': 'Albemarle County',
    'Chesapeake City': 'Chesapeake City',  # Large enough to be its own region
    'Colonial Heights City': 'Chesterfield County',
    'Covington City': 'Alleghany County',
    'Danville City': 'Pittsylvania County',
    'Emporia City': 'Greensville County',
    'Fairfax City': 'Fairfax County',
    'Falls Church City': 'Arlington County',
    'Franklin City': 'Southampton County',
    'Fredericksburg City': 'Spotsylvania County',
    'Galax City': 'Grayson County',
    'Hampton City': 'Hampton City',  # Part of Hampton Roads
    'Harrisonburg City': 'Rockingham County',
    'Hopewell City': 'Prince George County',
    'Lexington City': 'Rockbridge County',
    'Lynchburg City': 'Campbell County',
    'Manassas City': 'Prince William County',
    'Manassas Park City': 'Prince William County',
    'Martinsville City': 'Henry County',
    'Newport News City': 'Newport News City',  # Part of Hampton Roads
    'Norfolk City': 'Norfolk City',  # Part of Hampton Roads
    'Norton City': 'Wise County',
    'Petersburg City': 'Dinwiddie County',
    'Poquoson City': 'York County',
    'Portsmouth City': 'Portsmouth City',  # Part of Hampton Roads
    'Radford City': 'Montgomery County',
    'Richmond City': 'Henrico County',
    'Roanoke City': 'Roanoke County',
    'Salem City': 'Roanoke County',
    'Staunton City': 'Augusta County',
    'Suffolk City': 'Suffolk City',  # Large area
    'Virginia Beach City': 'Virginia Beach City',  # Large area
    'Waynesboro City': 'Augusta County',
    'Williamsburg City': 'James City County',
    'Winchester City': 'Frederick County',
    'West Point Town': 'King William County',
}

def get_county(division_name):
    """
    Extract county from division name.
    If it's already a county, return as-is.
    If it's a city or town, map it to the associated county.
    """
    # If it already ends with 'County', return it
    if 'County' in division_name:
        return division_name
    
    # If it's a city or town, look it up in the mapping
    if 'City' in division_name or 'Town' in division_name:
        print('itsno')
        co_return = city_to_county_map.get(division_name.strip())
        print(division_name)
        print(co_return)
        return co_return
    
    # Default: return as-is
    return None

# Apply to your dataframe
reading_df['county'] = reading_df['division_name'].apply(get_county)

# Display the result
print(reading_df.head(10).to_string())

itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County
itsno
Alexandria City 
Arlington County


In [171]:
test = reading_df[reading_df['division_name'].str.contains('city', case=False)]
# Display the result
print(test.sort_values(by='school_name').to_string())

     full_code  division_number                    division_name  school_number                                           school_name          subject english_learners test_source level pass_rate_24 pass_rate_25     enrollment_24     enrollment_25  eln_school?                           county
2559   112-500              112                    Hampton City             500                            A.W.E. Bassette Elementary  English:Reading                N         SOL    ES        61.68        65.77               484               472        False                     Hampton City
2560   112-500              112                    Hampton City             500                            A.W.E. Bassette Elementary  English:Reading                Y         SOL    ES          >50        58.33                13                12        False                     Hampton City
2553   112-160              112                    Hampton City             160                                   Aber

In [172]:
reading_df.to_csv('C:/Users/clutz/Downloads/va_eln_reading_results_v2.csv', index=False)

In [122]:
codes_no_level=pd.DataFrame({'full_code':idk})

codes_no_level['']

KeyError: ''

In [ ]:
git clone https://github.com/DjangoCRM/django-crm.git /.app_dev